Ondřej Hladůvka  

If you want to run code in this notebook, you can find it here: https://git.hladu.xyz/hladu357/TalTech_crypt/src/branch/master/hw2

## Task 1 Confusion and diffusion
From the lectures, you learned about importance of confusion and diffusion principles for the block ciphers. Let us examine them in more details. Assume you need to analyse
properties of Vigenere cipher.

1. Encrypt message THEWANDCHOOSESTHEWIZARD with key MAGIC.

In [25]:
def vigenere_enc(pt : str, key : str):
    pt_int  = [ord(i) - ord('A') for i in pt]
    key_int = [ord(i) - ord('A') for i in key]

    ct_int = [(char + key_int[idx % len(key_int)]) % 26 for idx, char in enumerate(pt_int)]
    ct     = [chr(i + ord('A')) for i in ct_int]
    return ct

pt = "THEWANDCHOOSESTHEWIZARD"
key = "MAGIC"
ct = vigenere_enc(pt, key)

print("ciphertext: ", "".join(ct))

ciphertext:  FHKECZDIPQASKAVTECQBMRJ


2. Suppose we change one letter (W becomes L) in the plaintext to get THEWANDCHOOSESTHE L IZARD.
How may letters of the ciphertext are changed? Is the diffusion property achieved?

In [26]:
idx = 17
pt2 = pt[:idx] + "L" + pt[(idx + 1):]
ct2 = "".join(vigenere_enc(pt2, key))

print(f"Witch changed plaintext at index {idx}")
print(f"New ciphertext is: {ct2}")

for idx, (a, b) in enumerate(zip(ct, ct2)):
    if (a != b):
        print(f"character changes at index {idx} {a} -> {b}")
print("diffusion is not achieved, as the plaintext's change effects the ciphertext in structured way exploitable by cryptanalysis")

Witch changed plaintext at index 17
New ciphertext is: FHKECZDIPQASKAVTERQBMRJ
character changes at index 17 C -> R
diffusion is not achieved, as the plaintext's change effects the ciphertext in structured way exploitable by cryptanalysis


3. Suppose we change one letter in key (G becomes N). How may letters of the ciphertext are changed?
Is confusion property achieved?

In [27]:
import math
print("it would change lower whole part n / k letters where n is length of plaintext and k is length of the key")
n = len(pt)
k = len(key)
print(f"floor(n / k) = floor({n} / {k}) = {math.floor(n/k)}")
print("confusion is not achieved, as the key's effect on the ciphertext is structured and exploitable by cryptanalysis")

it would change lower whole part n / k letters where n is length of plaintext and k is length of the key
floor(n / k) = floor(23 / 5) = 4
confusion is not achieved, as the key's effect on the ciphertext is structured and exploitable by cryptanalysis


## Task 2. Pseudorandom function 
Let F ∶ {0, 1}
n × {0, 1}
n → {0, 1}
n
be a secure PRF. Do the following
functions satisfy definition of pseudo-random function?

1. F′(k, m) = F(k, m) || 0^n, where 0^n is a zero string of length n

In [34]:
# no efficient algorithm can distinguish (with significant advantage)
# between a function chosen randomly from the PRF family and a random oracle
import random
import string
msg_len = 4

def prf1(input):
    return [random.randint(0, 1) for _ in range(len(input))] + [0] * len(input)

def challenger1(input):
    if (random.choice([True, False])): # random oracle
        return [random.randint(0, 1) for _ in range(len(input) * 2)], True
    else: # tested function
        return prf1(input), False

words = ["abcd", "efgh", "ijkl", "mnop", "qrst", "uvwx"]
def adversary1(w, verbose=True):
        response = challenger1(w)
        if verbose: print(f"adverasry got response: {response[0]}")
        
        if all(x == 0 for x in response[0][len(w):]):
            if verbose: print(f"he guessed it is not oraculum - its {response[1] == False}\n")
            return response[1] == False
        else:
            if verbose: print(f"he guessed it is oraculum - its {response[1] == True}\n")
            return response[1] == True


print("Adversary with strategy that guesses its not oraculum if last n bits of the message are all zeros")
print("can be wrong only if oraculum, was used (1/2 chance) and it generated last last n bits of the message all zeros (2^-n)")
print("Chance of this is 2 to the power of minus (message length + 1)")
print("With growing n, this function converges to 0 -> F' is not secure PRF\n\n")

chance = pow(2,-msg_len)
print(f"We can simulate this, assumming python random is close enough to random oraculum")
print(f"For message {msg_len} characters long, its only a {chance} chance")
print(f"but only if random oracle is selected so times 0.5 -> {chance/2} chance")

for w in words:
    adversary1(w)

tests = 1000
passed = 0
print(f"we can meassure the prediction:")
for i in range(0, tests):
    msg = ''.join(random.choices(string.ascii_lowercase, k=msg_len))
    passed += adversary1(msg, False)

print(f"adversary passed {passed} out of {tests} tests, which is {round(1 - (passed / tests),5)} chance of failure")

Adversary with strategy that guesses its not oraculum if last n bits of the message are all zeros
can be wrong only if oraculum, was used (1/2 chance) and it generated last last n bits of the message all zeros (2^-n)
Chance of this is 2 to the power of minus (message length + 1)
With growing n, this function converges to 0 -> F' is not secure PRF


We can simulate this, assumming python random is close enough to random oraculum
For message 4 characters long, its only a 0.0625 chance
but only if random oracle is selected so times 0.5 -> 0.03125 chance
adverasry got response: [1, 1, 1, 1, 0, 0, 0, 0]
he guessed it is not oraculum - its False

adverasry got response: [0, 1, 0, 0, 0, 0, 0, 0]
he guessed it is not oraculum - its True

adverasry got response: [0, 0, 1, 0, 0, 0, 0, 0]
he guessed it is not oraculum - its True

adverasry got response: [1, 1, 1, 0, 0, 0, 0, 0]
he guessed it is not oraculum - its True

adverasry got response: [0, 0, 0, 1, 0, 0, 0, 0]
he guessed it is not oraculum

2. F′(k, m∣∣m′) = F(k, m)∣∣F(k, m′ ⊕ 0^n), where 0^n is a zero string of length n

Since x ⊕ 0 = x, we can simplify
F' := F(k, m∣∣m′) = F'(k, m)∣∣F'(k, m′)

With startegy:  
choose message x
x = a^n (where n is power of 2)

get message y  
if message is repeating bit => adversary guess its not oraculum  
y = F'(a^(n/2) || F'(a^(n/2)) = F'(a^(n/4)) || F'(a^(n/4)) || F'(a^(n/4)) || F'(a^(n/4)) = ... = F'(a)^n

else => guess its oraculum

Only way adversary could be wrong if oraculum generated n repeating bits, chance of this is 2^(-n)  
With growing n, this function converges to 0 -> F' is not secure PRF

3. F′(k, m∣∣m′) = F(k, 0∣∣m) ⊕ F(k, m′∣∣1), where m, m′∈ {0, 1}^(n−1)

With startegy:
querying two messages x_1, x_2  
x_1 = 0^(n-1)||0^(n-1)  
x_2 = 0^(n-1)||1^(n-1)  
  
get messages y_1, y_2  


if y_1 ⊕ y_2 == 0^n => adversary guess its not oraculum  
y_1 ⊕ y_2 = (F(k,0||0^(n−1)) ⊕ F(k,0^(n−1)||1)) ⊕ (F(k,0||0^(n−1)) ⊕ F(k,1^(n−1||1))  
y_1 ⊕ y_2 = F(k,0||1^(n−1)) ⊕ F(k,1^(n−1||1)  
  
else => guess its oraculum  
  
chance of two random oraculum outputs being inverse (y_1 ⊕ y_2 == 0^n) is 2^(-n)  
With growing n, this function converges to 0 -> F' is not secure PRF

## Task 3
Output feedback mode Consider the following permutation cipher – instead of permuting plaintext letters to get ciphertext, you are first required to convert plaintext letters to binary form and next you
permute bits according to the key. Letter H becomes encrypted to T with key (5, 1, 2, 4, 3). Let us view it as
block cipher with block length 5 bits.

In [29]:
def perm_enc(pt: list[int], key: list[int]):
    blocksize = 5
    ct = [0] * blocksize
    for idx in range(0, blocksize):
        ct[idx] = pt[key[idx] - 1]
    return ct

def convert_str(pt: list[int]): # converts to list of binary blocks
    bit_array = []
    for char in pt:
        bits = bin(ord(char) - ord('A'))[2:][-5:].zfill(5)
        bit_array.append([int(bit) for bit in bits])
    return bit_array

def ofb(pt, key, iv, cipher):
    ct = []
    for block in pt:
        iv = cipher(iv, key)
        ct.append([x ^ y for (x,y) in zip(iv, block)]) # encrypted iv into block
    return ct

key = [5, 1, 2, 4, 3]

1. Encrypt world DOG with key (4, 1, 3, 5, 2) using permutation cipher in OFB mode with iv = 01011. Leave
result as a binary string.

In [30]:
pt = convert_str(['D', 'O', 'G'])
key = [4, 1, 3, 5, 2]
iv = [0, 1, 0, 1, 1]
ct = ofb(pt, key, iv, perm_enc)
print(f"plaintext:  {pt}")
print(f"ciphertext: {ct}")

plaintext:  [[0, 0, 0, 1, 1], [0, 1, 1, 1, 0], [0, 0, 1, 1, 0]]
ciphertext: [[1, 0, 0, 0, 0], [1, 0, 1, 0, 0], [1, 1, 1, 1, 1]]


2. Flip 5-th bit of received ciphertext (0 becomes 1 and vice versa). Now decrypt modified ciphertext. How
many bits in the plaintext get changed?

In [31]:
import copy
ct2 = copy.deepcopy(ct)
ct2[0][4] ^= 1
pt2 = ofb(ct2, key, iv, perm_enc)

print(f"original ciphertext: {ct}")
print(f"modified ciphertext:  {ct2}")
print(f"original plaintext:  {pt}")
print(f"modified plaintext:   {pt2}")
print(f"one bit also flipped -> no diffusion")

original ciphertext: [[1, 0, 0, 0, 0], [1, 0, 1, 0, 0], [1, 1, 1, 1, 1]]
modified ciphertext:  [[1, 0, 0, 0, 1], [1, 0, 1, 0, 0], [1, 1, 1, 1, 1]]
original plaintext:  [[0, 0, 0, 1, 1], [0, 1, 1, 1, 0], [0, 0, 1, 1, 0]]
modified plaintext:   [[0, 0, 0, 1, 0], [0, 1, 1, 1, 0], [0, 0, 1, 1, 0]]
one bit also flipped -> no diffusion


3. Flip the first bit of the IV iv′ = 11011, decrypt ciphertext from Step 1 with iv′
. How many bits in the
plaintext get changed?

In [32]:
iv[0] ^= 1
pt3 = ofb(ct, key, iv, perm_enc)

print(f"original plaintext:  {pt}")
print(f"modified plaintext:   {pt3}")
print(f"one bit per block also flipped")

original plaintext:  [[0, 0, 0, 1, 1], [0, 1, 1, 1, 0], [0, 0, 1, 1, 0]]
modified plaintext:   [[0, 1, 0, 1, 1], [0, 1, 1, 1, 1], [0, 0, 1, 0, 0]]
one bit per block also flipped


## Task 4
Consider the encryption of n−block message m = m1∣∣m2∣∣. . .∣∣m_n by some block cipher E in
CFB mode. Let use denote ciphertext produced by E as c = c1∣∣c2∣∣. . .∣∣cn. Show which information about
the plaintext can be extracted if we get a collision: ci = cj
, where i ≠ j.

#### In OFB mode:  
Ek(iv)^n := Ek( Ek( ... Ek(iv))) n times
ct_n = pt_n ⊕ Ek(iv)^n

ct_i == ct_j implies =>  
Ek(iv)^i == Ek(iv)^j =>  
pt_i ⊕ pt_j == Ek(iv)^(i-1) ⊕ Ek(iv)^(j-1)

## Task 5
Show that Pigpen cipher defined below is not IND-OT-CPA secure (where adversary is allowed to
do only one query to the challenger in the IND-CPA game).
The pigpen cipher uses graphical symbols assigned according to a key in the diagram below1
(NOTE: Positions
of the letters in the diagrams are random and not known to adversary):

#### Indistinguishability under One-Time Chosen Plaintext Attack definition:
1. The challenger generates a secret key K
2. The adversary submits two distinct plaintexts Pt_0, Pt_1 of equal length to the challenger
3. The challenger selects a random bit b ∈ {0,1}, resulting in ciphertext Ct = Ek(M_b) being sent to the adversary
4. Based on the Ct, the adversary guess b′ ∈ {0,1} for the value of b
5. Scheme is not secure if no adversary has a non-negligible advantage in guessing over 1/2

#### Adversary strategy:
We can expoit Pigpen cipher being monoalphabetic
Adversary will send one message with repeating characters and another with each character unique  
M_0 := "AA"  
M_1 := "AB"  

If Ct is some repeating characters => choose 0  
Else => choose 1  

This strategy will work every time thanks to monoalphabeticity